In [1]:
!nvidia-smi

Mon Aug 15 18:34:16 2022       
+-----------------------------------------------------------------------------+
| NVIDIA-SMI 460.32.03    Driver Version: 460.32.03    CUDA Version: 11.2     |
|-------------------------------+----------------------+----------------------+
| GPU  Name        Persistence-M| Bus-Id        Disp.A | Volatile Uncorr. ECC |
| Fan  Temp  Perf  Pwr:Usage/Cap|         Memory-Usage | GPU-Util  Compute M. |
|                               |                      |               MIG M. |
|===============================+======================+======================|
|   0  Tesla T4            Off  | 00000000:00:04.0 Off |                    0 |
| N/A   60C    P8    13W /  70W |      0MiB / 15109MiB |      0%      Default |
|                               |                      |                  N/A |
+-------------------------------+----------------------+----------------------+
                                                                               
+-------

In [2]:
! pip install datasets transformers rouge-score nltk py7zr
! pip install wandb -qq

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
     |████████████████████████████████| 365 kB 4.7 MB/s 
     |████████████████████████████████| 4.7 MB 68.3 MB/s 
     |████████████████████████████████| 64 kB 3.9 MB/s 
     |████████████████████████████████| 141 kB 61.7 MB/s 
     |████████████████████████████████| 115 kB 63.0 MB/s 
     |████████████████████████████████| 212 kB 73.6 MB/s 
     |████████████████████████████████| 101 kB 12.4 MB/s 
     |████████████████████████████████| 596 kB 73.3 MB/s 
     |████████████████████████████████| 127 kB 69.5 MB/s 
     |████████████████████████████████| 6.6 MB 59.3 MB/s 
     |████████████████████████████████| 2.3 MB 33.4 MB/s 
     |████████████████████████████████| 92 kB 11.5 MB/s 
     |████████████████████████████████| 50 kB 7.1 MB/s 
     |████████████████████████████████| 357 kB 68.6 MB/s 
     |████████████████████████████████| 379 kB 71.2 MB/s 
     |███████████████████████████████

In [3]:
import wandb
wandb.login()

<IPython.core.display.Javascript object>

wandb: Logging into wandb.ai. (Learn how to deploy a W&B server locally: https://wandb.me/wandb-server)
wandb: You can find your API key in your browser here: https://wandb.ai/authorize
wandb: Paste an API key from your profile and hit enter, or press ctrl+c to quit: 

··········


wandb: Appending key for api.wandb.ai to your netrc file: /root/.netrc


True

In [4]:
%env WANDB_PROJECT=bart_large_xsum_samsum

env: WANDB_PROJECT=bart_large_xsum_samsum


In [5]:
model_checkpoint = "facebook/bart-large-xsum"

## Loading the dataset

In [6]:
from datasets import load_dataset, load_metric

raw_datasets = load_dataset("samsum")
metric = load_metric("rouge")

Generating train split:   0%|          | 0/14732 [00:00<?, ? examples/s]

Generating test split:   0%|          | 0/819 [00:00<?, ? examples/s]

Generating validation split:   0%|          | 0/818 [00:00<?, ? examples/s]

Dataset samsum downloaded and prepared to /root/.cache/huggingface/datasets/samsum/samsum/0.0.0/f1d7c6b7353e6de335d444e424dc002ef70d1277109031327bc9cc6af5d3d46e. Subsequent calls will reuse this data.


  0%|          | 0/3 [00:00<?, ?it/s]

## Preprocessing the data

In [7]:
from transformers import AutoTokenizer
    
tokenizer = AutoTokenizer.from_pretrained(model_checkpoint)

In [8]:
max_input_length = 512
max_target_length = 128

def preprocess_function(examples):
    inputs = [doc for doc in examples["dialogue"]]
    model_inputs = tokenizer(inputs, max_length=max_input_length, truncation=True)

    # Setup the tokenizer for targets
    with tokenizer.as_target_tokenizer():
        labels = tokenizer(examples["summary"], max_length=max_target_length, truncation=True)

    model_inputs["labels"] = labels["input_ids"]
    return model_inputs

In [9]:
tokenized_datasets = raw_datasets.map(preprocess_function, batched=True)

  0%|          | 0/15 [00:00<?, ?ba/s]

  0%|          | 0/1 [00:00<?, ?ba/s]

  0%|          | 0/1 [00:00<?, ?ba/s]

## Fine-tuning the model

In [10]:
from transformers import AutoModelForSeq2SeqLM, DataCollatorForSeq2Seq, Seq2SeqTrainingArguments, Seq2SeqTrainer

model = AutoModelForSeq2SeqLM.from_pretrained(model_checkpoint)

In [45]:
batch_size = 4
args = Seq2SeqTrainingArguments(
    "test-dialogue-summarization",
    evaluation_strategy = "epoch",
    learning_rate=2e-5,
    per_device_train_batch_size=batch_size,
    per_device_eval_batch_size=batch_size,
    gradient_accumulation_steps=2,
    weight_decay=0.01,
    save_total_limit=2,
    num_train_epochs=3,
    predict_with_generate=True,
    fp16=True,
    # output_dir="my-awesome-model",
    push_to_hub=True,
    report_to="wandb",  # enable logging to W&B
    run_name="bart-large-xsum-samsum"  # name of the W&B run (optional)
)

PyTorch: setting up devices


In [38]:
data_collator = DataCollatorForSeq2Seq(tokenizer, model=model)

In [13]:
import nltk
import numpy as np

def compute_metrics(eval_pred):
    predictions, labels = eval_pred
    decoded_preds = tokenizer.batch_decode(predictions, skip_special_tokens=True)
    # Replace -100 in the labels as we can't decode them.
    labels = np.where(labels != -100, labels, tokenizer.pad_token_id)
    decoded_labels = tokenizer.batch_decode(labels, skip_special_tokens=True)
    
    # Rouge expects a newline after each sentence
    decoded_preds = ["\n".join(nltk.sent_tokenize(pred.strip())) for pred in decoded_preds]
    decoded_labels = ["\n".join(nltk.sent_tokenize(label.strip())) for label in decoded_labels]
    
    result = metric.compute(predictions=decoded_preds, references=decoded_labels, use_stemmer=True)
    # Extract a few results
    result = {key: value.mid.fmeasure * 100 for key, value in result.items()}
    
    # Add mean generated length
    prediction_lens = [np.count_nonzero(pred != tokenizer.pad_token_id) for pred in predictions]
    result["gen_len"] = np.mean(prediction_lens)
    
    return {k: round(v, 4) for k, v in result.items()}

In [14]:
trainer = Seq2SeqTrainer(
    model,
    args,
    train_dataset=tokenized_datasets["train"],
    eval_dataset=tokenized_datasets["validation"],
    data_collator=data_collator,
    tokenizer=tokenizer,
    compute_metrics=compute_metrics
)

Using cuda_amp half precision backend


In [15]:
import nltk
nltk.download('punkt')

[nltk_data] Downloading package punkt to /root/nltk_data...
[nltk_data]   Unzipping tokenizers/punkt.zip.


True

In [16]:
trainer.train()

The following columns in the training set don't have a corresponding argument in `BartForConditionalGeneration.forward` and have been ignored: id, dialogue, summary. If id, dialogue, summary are not expected by `BartForConditionalGeneration.forward`,  you can safely ignore this message.
/usr/local/lib/python3.7/dist-packages/transformers/optimization.py:310: FutureWarning: This implementation of AdamW is deprecated and will be removed in a future version. Use the PyTorch implementation torch.optim.AdamW instead, or set `no_deprecation_warning=True` to disable this warning
  FutureWarning,
***** Running training *****
  Num examples = 14732
  Num Epochs = 3
  Instantaneous batch size per device = 4
  Total train batch size (w. parallel, distributed & accumulation) = 8
  Gradient Accumulation steps = 2
  Total optimization steps = 5523
Automatic Weights & Biases logging enabled, to disable set os.environ["WANDB_DISABLED"] = "true"


wandb: Currently logged in as: ayoola. Use `wandb login --relogin` to force relogin


Saving model checkpoint to test-dialogue-summarization/checkpoint-500
Configuration saved in test-dialogue-summarization/checkpoint-500/config.json
Model weights saved in test-dialogue-summarization/checkpoint-500/pytorch_model.bin
tokenizer config file saved in test-dialogue-summarization/checkpoint-500/tokenizer_config.json
Special tokens file saved in test-dialogue-summarization/checkpoint-500/special_tokens_map.json
Saving model checkpoint to test-dialogue-summarization/checkpoint-1000
Configuration saved in test-dialogue-summarization/checkpoint-1000/config.json
Model weights saved in test-dialogue-summarization/checkpoint-1000/pytorch_model.bin
tokenizer config file saved in test-dialogue-summarization/checkpoint-1000/tokenizer_config.json
Special tokens file saved in test-dialogue-summarization/checkpoint-1000/special_tokens_map.json
Saving model checkpoint to test-dialogue-summarization/checkpoint-1500
Configuration saved in test-dialogue-summarization/checkpoint-1500/config.js

TrainOutput(global_step=5523, training_loss=1.1176997911189748, metrics={'train_runtime': 4282.7561, 'train_samples_per_second': 10.32, 'train_steps_per_second': 1.29, 'total_flos': 2.609612124409037e+16, 'train_loss': 1.1176997911189748, 'epoch': 3.0})

In [17]:
trainer.evaluate()

The following columns in the evaluation set don't have a corresponding argument in `BartForConditionalGeneration.forward` and have been ignored: id, dialogue, summary. If id, dialogue, summary are not expected by `BartForConditionalGeneration.forward`,  you can safely ignore this message.
***** Running Evaluation *****
  Num examples = 818
  Batch size = 4


{'eval_loss': 1.4711707830429077,
 'eval_rouge1': 54.4211,
 'eval_rouge2': 29.5361,
 'eval_rougeL': 45.1176,
 'eval_rougeLsum': 50.0659,
 'eval_gen_len': 30.4315,
 'eval_runtime': 238.6829,
 'eval_samples_per_second': 3.427,
 'eval_steps_per_second': 0.859,
 'epoch': 3.0}

In [18]:
wandb.finish()

In [22]:
from huggingface_hub import notebook_login

In [23]:
notebook_login()

Login successful
Your token has been saved to /root/.huggingface/token
Authenticated through git-credential store but this isn't the helper defined on your machine.
You might have to re-authenticate when pushing to the Hugging Face Hub. Run the following command in your terminal in case you want to set this credential helper as the default

git config --global credential.helper store


In [43]:
model.push_to_hub("clyde")

Configuration saved in clyde/config.json
Model weights saved in clyde/pytorch_model.bin


Upload file optimizer.pt:   0%|          | 3.33k/3.03G [00:00<?, ?B/s]

Upload file training_args.bin:  98%|#########7| 3.34k/3.42k [00:00<?, ?B/s]

Upload file scheduler.pt: 100%|##########| 623/623 [00:00<?, ?B/s]

Upload file rng_state.pth:  24%|##3       | 3.34k/14.2k [00:00<?, ?B/s]

Upload file scaler.pt: 100%|##########| 559/559 [00:00<?, ?B/s]

remote: Scanning LFS files for validity, may be slow...        
remote: LFS file scan complete.        
To https://huggingface.co/Ayoola/clyde
   1cf1d86..7d9a15b  main -> main

remote: LFS file scan complete.        
To https://huggingface.co/Ayoola/clyde
   1cf1d86..7d9a15b  main -> main



'https://huggingface.co/Ayoola/clyde/commit/7d9a15bad003beb24e7c06238c5a4857c505538e'

In [44]:
from transformers import pipeline

summarizer = pipeline("summarization", model="Ayoola/clyde")
conversation = '''che: Hey, have you built the model?
Ayo: Lemme check
Ayo: Sorry, i have not.
Ayo: I will tomorrow
Ayo: i think we need more data
Ayo: but i may be wrong
Ayo: it is just an hypothesis
che: If you say so..
che: i am working converting the transcriptions to the right format
Ayo: Awesome 🙂
che: see you soon
che: Bye
Ayo: Bye bye                                       
'''
summarizer(conversation)

loading configuration file https://huggingface.co/Ayoola/clyde/resolve/main/config.json from cache at /root/.cache/huggingface/transformers/3925684a81d704d784ffab4bdb4097fcb08c20930badd3337c07782d0eb5d666.9b8c0031ba05106ba501a98678111e6eb1447b983b16dfba9960cba29742333d
Model config BartConfig {
  "_name_or_path": "Ayoola/clyde",
  "_num_labels": 3,
  "activation_dropout": 0.0,
  "activation_function": "gelu",
  "add_bias_logits": false,
  "add_final_layer_norm": false,
  "architectures": [
    "BartForConditionalGeneration"
  ],
  "attention_dropout": 0.0,
  "bos_token_id": 0,
  "classif_dropout": 0.0,
  "classifier_dropout": 0.0,
  "d_model": 1024,
  "decoder_attention_heads": 16,
  "decoder_ffn_dim": 4096,
  "decoder_layerdrop": 0.0,
  "decoder_layers": 12,
  "decoder_start_token_id": 2,
  "dropout": 0.1,
  "early_stopping": true,
  "encoder_attention_heads": 16,
  "encoder_ffn_dim": 4096,
  "encoder_layerdrop": 0.0,
  "encoder_layers": 12,
  "eos_token_id": 2,
  "eos_token_ids": [
 

storing https://huggingface.co/Ayoola/clyde/resolve/main/tokenizer_config.json in cache at /root/.cache/huggingface/transformers/2febc93d635fa6b51c8bcb6ca66b8c0e18f9e315b1b08d5d07cb4134147f68a2.637741d8cb9d1bcc8a4ac07b1bad9c87fe6e109d6d1c8a9ac58c04819c682ef4
creating metadata file for /root/.cache/huggingface/transformers/2febc93d635fa6b51c8bcb6ca66b8c0e18f9e315b1b08d5d07cb4134147f68a2.637741d8cb9d1bcc8a4ac07b1bad9c87fe6e109d6d1c8a9ac58c04819c682ef4
https://huggingface.co/Ayoola/clyde/resolve/main/merges.txt not found in cache or force_download set to True, downloading to /root/.cache/huggingface/transformers/tmpz0qtavzq


storing https://huggingface.co/Ayoola/clyde/resolve/main/merges.txt in cache at /root/.cache/huggingface/transformers/f32ef59697c892097dc72173e699e05327a6b57ef72bc15fc6577309f82e1445.f5b91da9e34259b8f4d88dbc97c740667a0e8430b96314460cdb04e86d4fc435
creating metadata file for /root/.cache/huggingface/transformers/f32ef59697c892097dc72173e699e05327a6b57ef72bc15fc6577309f82e1445.f5b91da9e34259b8f4d88dbc97c740667a0e8430b96314460cdb04e86d4fc435
https://huggingface.co/Ayoola/clyde/resolve/main/tokenizer.json not found in cache or force_download set to True, downloading to /root/.cache/huggingface/transformers/tmp1rd8i6kp


storing https://huggingface.co/Ayoola/clyde/resolve/main/tokenizer.json in cache at /root/.cache/huggingface/transformers/05351f3167b720d945aee44c7d9cf851a3f38475914d6e052cbb661f88e822d8.e2f4eedc407009ae71961202385942a093ae25045c2f8223c20d64be0e0c9626
creating metadata file for /root/.cache/huggingface/transformers/05351f3167b720d945aee44c7d9cf851a3f38475914d6e052cbb661f88e822d8.e2f4eedc407009ae71961202385942a093ae25045c2f8223c20d64be0e0c9626
https://huggingface.co/Ayoola/clyde/resolve/main/special_tokens_map.json not found in cache or force_download set to True, downloading to /root/.cache/huggingface/transformers/tmpy4he0ksd


storing https://huggingface.co/Ayoola/clyde/resolve/main/special_tokens_map.json in cache at /root/.cache/huggingface/transformers/a62550b5220632506995aca304dd395e8cf798c15fbfebc71e30c58f9a150602.50c9a6a3342271e7e900bb03520d7f844b78e2b2ef8352a0239b688c7d12bdc6
creating metadata file for /root/.cache/huggingface/transformers/a62550b5220632506995aca304dd395e8cf798c15fbfebc71e30c58f9a150602.50c9a6a3342271e7e900bb03520d7f844b78e2b2ef8352a0239b688c7d12bdc6
loading file https://huggingface.co/Ayoola/clyde/resolve/main/vocab.json from cache at None
loading file https://huggingface.co/Ayoola/clyde/resolve/main/merges.txt from cache at /root/.cache/huggingface/transformers/f32ef59697c892097dc72173e699e05327a6b57ef72bc15fc6577309f82e1445.f5b91da9e34259b8f4d88dbc97c740667a0e8430b96314460cdb04e86d4fc435
loading file https://huggingface.co/Ayoola/clyde/resolve/main/tokenizer.json from cache at /root/.cache/huggingface/transformers/05351f3167b720d945aee44c7d9cf851a3f38475914d6e052cbb661f88e822d8.e2f

[{'summary_text': "Ayo hasn't built the model yet. Che is working on converting the transcriptions to the right format."}]